Stand 29.10.2023, S. Mack
# Objektorientiert animierte Plots mit Matplotlib erstellen
Dieses Jupyter Notebook behandelt nur die Animation von Matplotlib-Plots.
Alles Andere finden Sie im Jupyter Notebook [**matplotlibOop**](https://nbviewer.jupyter.org/github/StefanMack/Matplotlib/blob/master/matplotlibOop.ipynb).

Wenn der zeitliche Verlauf eines Signals von Interesse ist, kann man diesen sehr eindrucksvoll als animierten Plot darstellen.  

Im ersten Beispiel unten wird ein Phasenversatz für eine Sinusschwingung dargestellt:  
Als Erstes wird die Funktion ``init_func`` (hier ``init()``) ausgeführt, die die vorherigen Datenpunkte aus dem Plot löscht. Die eigentlich animierte Funktion ist ``func`` (hier ``animate()``), welche für die Plot-Kurve ``line`` die neuen Werten berechnet und ihr zuweist. Der Parameter ``frames`` ist hier eine Ganzzahl, die angibt, wie viele Frames mit jeweils der Periode ``intervall`` dargestellt werden.
(Im zweiten Beispiel ist ``frames`` übrigens dann keine Ganzzahl mehr sondern ein Iterator, welcher die aktuellen Daten liefert.)  
**Achtung**: Nach dem Start dieser Animation mit Shift + Enter kann es je nach Größe der darzustellenden Daten einige Sekunden dauern bis der animierte Plot erscheint.

In [1]:
%matplotlib inline
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from IPython.display import HTML

x = np.arange(0, 2*np.pi, 0.01)
fig, ax = plt.subplots()
plt.close(); # damit kein weiterer leerer Plot dargestellt wird
ax.set(xlabel='Phase [rad]', ylabel='Amplitude', title='Animation Phasenversatz')
line, = ax.plot(x, np.sin(x))

def init():  # um beim Start die alten Werte zu löschen
    line.set_ydata([np.nan] * len(x))
    return line,

def animate(i):
    line.set_ydata(np.sin(x + 5*i / 100))  # neue y-Werte berechnen
    return line,
# interval: Frameperiode in ms, frames: Zahl Frames (alt. save_count=50) da kein Iterator, blit: Befehl Grafikkarte
ani = animation.FuncAnimation(fig, func=animate, init_func=init, frames=50, interval=100, repeat=False, blit=True)
HTML(ani.to_jshtml())

Als zweites Beispiel zeigt die folgende Animation eine gedämpfte Schwingung.  
Hier werden für jeden Frame (mit Periode ``interval`` in Millisekunden) zuerst die Datenwerte vom Iterator ``frames`` (hier ``data_gen()``) einzeln abgeholt und gelangen dann zur eigentlich animierten Funktion ``func`` (hier ``run()``), welche diese als neuen Datenpunkt jeweils dem Plot hinzufügt. Vorher wird einmalig beim Start der Animation die Funktion ``init_func`` (hier ``init()`` zum Löschen der vorherigen Datenpunkte) ausgeführt.  
Das mit dem Iterator kann man sich so vorstellen, dass dieser in dem Beispiel unten 100 Datenwerte erzeugt, welche bei jedem neuen Frame um einen Index weiter iteriert werden.  

Solch eine Iteratorfunktion kann auch eine While-Schleife beinhalten, welche z.B. immer den aktuellen Messwert über die Schnittstelle eines Messgeräts ausliest. Nachfolgend ist als Beispiel hierzu der Python-Code einer solchen Funktion für das serielle Auslesen eines Arduino-AD-Wandlers dargestellt:
```python
def getAdcVal(): # neuen Datenpunkt von serieller Schnittstelle lesen
    port.flushInput() # seriellen Puffer leeren
    port.write(b'\n') # ADC-Messung Arduino anfordern
    result = int(port.readline()) # von Schnittstelle bis \n lesen (Byte Array)
    return(result)

def data_gen(): # muss Iterator sein, daher yield und die While-Schleife
    while True:
        adcVal = getAdcVal()
        yield adcVal 
```
**Achtung**: Nach dem Start dieser Animation auch hier bitte etwas warten.

In [2]:
def data_gen(t=0,n_data=100): # erzeugt ein "Iterative" mit n_data Datensätzen
    cnt = 0
    while cnt < n_data:
        cnt += 1
        t += 0.1
        yield t, np.sin(2*np.pi*t) * np.exp(-t/5.)
        
def init(): # löscht vorherige Datenpunkte
    ax.set_ylim(-1.1, 1.1)
    ax.set_xlim(0, 10)
    del xdata[:]
    del ydata[:]
    line.set_data(xdata, ydata)
    return line,

def run(data): # wird für jeden Frame ausgeführt mit dem Rückgabewert von data_gen()
    t, y = data
    xdata.append(t)
    ydata.append(y)
    line.set_data(xdata, ydata)
    return line,

fig, ax = plt.subplots()
plt.close(); 
line, = ax.plot([], [], lw=2)
ax.grid()
ax.set(xlabel='Zeit [s]', ylabel='Amplitude [V]', title='Animation gedämpfte Schwingung')
xdata, ydata = [], []

ani = animation.FuncAnimation(fig, func=run, frames=data_gen, init_func=init, interval=100, repeat=False, blit=False, cache_frame_data=False)
HTML(ani.to_jshtml())

In [3]:
barplot = np.array([0.3, 0.6, 1.0, 0.8, 0.6, 0.4, 0.2, 0, 0, 0]) # Array Balkenwerte
barplots = barplot # spaeterer Array-Stapel (eine Reihe pro Frame der Animation)

def move_bars(barplot, npos): # verschiebt Balkendiagramm um npos Positionen nach Rechts
    n = len(barplot)
    result = np.zeros(n)
    for i in range(n):
        result[i] = barplot[(i-npos) % n] # Modulo operator % bewirkt Pos 0 nach Pos 9
    return result


for i in range(30):
    barplot = move_bars(barplot, 1)
    barplots = np.vstack([barplots, barplot]) # neuer Balkenwert-Array auf Stapel

x = np.arange(len(barplot))
fig, ax = plt.subplots()
plt.close(); # damit kein leerer Plot gerendert wird


def animate(i):
    ax.cla()
    ax.set_ylim(0, 1.1)
    ax.set_xticks(x)
    ax.set_title('Animation Barplot Frame {}'.format(i+1))
    bars = ax.bar(x, barplots[i],zorder=3)
    ax.grid(zorder=0) # zorder damit Gitte hinter den Balken

anim = animation.FuncAnimation(fig, animate, frames=30, interval=300, repeat=False)  
HTML(anim.to_jshtml())